# RateMyProfessor Data Collection and Analysis

Welcome to the RateMyProfessor Data Collection and Analysis notebook! This notebook will guide you through the process of fetching professor data from the RateMyProfessor API, processing the data, and saving it for further analysis.

Whether you're a beginner or looking to understand how to interact with APIs and handle data in Python, this notebook is designed to provide a clear and comprehensive walkthrough.

## Table of Contents

1. [Introduction](#Introduction)
2. [Setup and Installation](#Setup-and-Installation)
3. [Configuration](#Configuration)
4. [Defining Helper Functions](#Defining-Helper-Functions)
5. [Data Fetching and Processing](#Data-Fetching-and-Processing)
6. [Addressing Rating Imbalance: Collecting Negative Ratings](#Addressing-Rating-Imbalance)
    - [Configuration for Negative Ratings](#Configuration-for-Negative-Ratings)
    - [Defining Helper Functions for Negative Ratings](#Defining-Helper-Functions-for-Negative-Ratings)
    - [Data Fetching and Processing for Negative Ratings](#Data-Fetching-and-Processing-for-Negative-Ratings)
7. [Data Merging and Finalization](#Data-Merging-and-Finalization)
8. [Conclusion](#Conclusion)
9. [Appendix: Fetching a Single Professor (Optional)](#Appendix)

## Introduction

In this notebook, we'll perform the following tasks:

- **Import necessary libraries:** We'll start by importing the required Python libraries.
- **Configure settings:** Define constants and parameters for data collection.
- **Define helper functions:** Create functions to handle logging, data validation, data extraction, and CSV operations.
- **Fetch and process data:** Use concurrency to efficiently fetch professor data from the API.
- **Address rating imbalance:** Collect additional data focusing on negative ratings to balance the dataset.
- **Save and merge data:** Store the collected data in CSV files and merge them for comprehensive analysis.

By the end of this notebook, you'll have a robust dataset containing detailed information about professors from RateMyProfessor, balanced in terms of positive and negative ratings.

## Setup and Installation

Before we begin, ensure that you have the necessary libraries installed. We'll be using the following Python libraries:

- `tqdm`: For displaying progress bars.
- `concurrent.futures`: To handle concurrent processing.
- `csv`: For CSV file operations.
- `logging`: For logging errors and debug information.
- `os`: To interact with the operating system.
- `pandas`: For data manipulation and analysis.

Additionally, ensure that the `RateMyProfessor_Database_APIs` module is correctly installed and accessible in your environment.

Let's import the necessary libraries.

In [ ]:
from tqdm import tqdm
import concurrent.futures
import csv
import RateMyProfessor_Database_APIs 
import logging
import os
import pandas as pd

## Configuration

Next, we'll define the configuration constants that will control how our data collection operates. These include the range of professor IDs to process, the target number of professors to collect, minimum ratings required, filenames for the CSV and log files, batch sizes for processing, and the number of worker threads for concurrency.

We'll set up separate configurations for collecting general professor ratings and for collecting negative ratings to address any imbalance in the dataset.

In [4]:
# # Configuration for General Professor Ratings
# START_ID_GENERAL = 100000
# END_ID_GENERAL = 2000000
# TARGET_PROFESSORS_GENERAL = 50000
# MIN_RATINGS_GENERAL = 20
CSV_FILENAME_GENERAL = 'professors_50k.csv'
# LOG_FILENAME_GENERAL = 'professor_data_fetch.log'
# BATCH_SIZE_GENERAL = 100  # Number of IDs to process concurrently
# MAX_WORKERS_GENERAL = 100  # Number of threads for concurrent processing

# Configuration for Negative Ratings
START_ID_NEGATIVE = 2000001
END_ID_NEGATIVE = 4000000  # Adjust as needed to reach 25,000 professors
TARGET_PROFESSORS_NEGATIVE = 25000
MIN_RATINGS_NEGATIVE = 20
NEGATIVE_RATING_THRESHOLD = 2.75
CSV_FILENAME_NEGATIVE = 'negative_professors_25346.csv'
LOG_FILENAME_NEGATIVE = 'negative_professor_data_fetch.log'
BATCH_SIZE_NEGATIVE = 100  # Number of IDs to process concurrently
MAX_WORKERS_NEGATIVE = 100  # Number of threads for concurrent processing

## Defining Helper Functions

To keep our code organized and modular, we'll define several helper functions:

1. **`setup_logging(log_filename)`:** Initializes the logging configuration to capture errors and debug information.
2. **`validate_ratings(ratings)`:** Ensures that all ratings have non-empty comments.
3. **`extract_professor_data(professor)`:** Extracts and flattens professor, school, and ratings data into a list of dictionaries suitable for CSV writing.
4. **`fetch_and_filter_professor(prof_id, config)`:** Fetches a professor by ID and applies filtering criteria based on the provided configuration.
5. **`initialize_csv(csv_filename, headers)`:** Initializes the CSV file with appropriate headers.
6. **`append_rows_to_csv(csv_filename, rows, headers)`:** Appends a list of dictionaries to the CSV file.
7. **`batched(iterable, n)`:** Yields successive n-sized batches from an iterable.

These functions will be used for both general and negative ratings data collection, with parameters allowing customization based on the specific requirements.

In [3]:
def setup_logging(log_filename):
    """
    Sets up logging to capture errors and debug information.
    """
    logging.basicConfig(
        filename=log_filename,
        filemode='a',
        format='%(asctime)s - %(levelname)s - %(message)s',
        level=logging.ERROR
    )

def validate_ratings(ratings):
    """
    Ensure that all ratings have a non-empty comment.
    """
    if not isinstance(ratings, list):
        logging.error("Ratings is not a list.")
        return False

    for rating in ratings:
        if not isinstance(rating, dict):
            logging.error("Rating is not a dictionary.")
            return False
        comment = rating.get('comment', '').strip()
        if not comment or comment.lower() == 'no comments':
            return False
    return True

def extract_professor_data(professor):
    """
    Extract and flatten professor, school, and ratings data.
    Returns a list of dictionaries, each representing a row for the CSV.
    """
    # Extract professor's basic information
    professor_data = {
        'professor_id': professor.legacy_id,
        'department': professor.department,
        'first_name': professor.first_name,
        'last_name': professor.last_name,
        'would_take_again_percent': professor.would_take_again_percent,
        'avg_rating': getattr(professor, 'avg_rating', None),
        'num_ratings': getattr(professor, 'num_ratings', None)
    }

    # Extract and flatten school information
    school_data = getattr(professor, 'school', {})
    if not isinstance(school_data, dict):
        logging.error(f"School data for professor ID {professor.legacy_id} is not a dict.")
        school_data = {}
    
    flattened_school_data = {
        'school_legacyId': school_data.get('legacyId'),
        'school_name': school_data.get('name'),
        'school_city': school_data.get('city'),
        'school_state': school_data.get('state'),
        'school_country': school_data.get('country'),
        'school_id': school_data.get('id'),
        'school_avgRating': school_data.get('avgRating'),
        'school_numRatings': school_data.get('numRatings')
    }

    # Combine professor and school data
    base_data = {**professor_data, **flattened_school_data}

    # Prepare rows for each rating
    rows = []
    if isinstance(professor.ratings, list):
        for rating in professor.ratings:
            if not isinstance(rating, dict):
                logging.error(f"Invalid rating format for professor ID {professor.legacy_id}.")
                continue
            row = base_data.copy()
            for key, value in rating.items():
                clean_key = f'rating_{key}'.replace(' ', '_')
                row[clean_key] = value
            rows.append(row)
    else:
        logging.error(f"Ratings for professor ID {professor.legacy_id} is not a list.")

    return rows

def fetch_and_filter_professor(prof_id, config):
    """
    Fetch a professor by ID and apply filtering criteria based on the provided configuration.
    Returns the extracted data if the professor meets the criteria, else None.
    """
    try:
        professor = RateMyProfessor_Database_APIs.fetch_a_professor(prof_id)
        
        if not professor:
            logging.error(f"No data found for professor ID {prof_id}.")
            return None

        # Fetch configuration parameters
        min_ratings = config.get('MIN_RATINGS')
        negative_threshold = config.get('NEGATIVE_RATING_THRESHOLD')
        is_negative = config.get('IS_NEGATIVE', False)

        # Check if professor has enough ratings
        num_ratings = getattr(professor, 'num_ratings', 0)
        if num_ratings < min_ratings:
            return None

        # If collecting negative ratings, check average rating threshold
        if is_negative:
            avg_rating = getattr(professor, 'avg_rating', None)
            if not isinstance(avg_rating, (int, float)):
                logging.error(f"Avg rating for professor ID {prof_id} is not a number.")
                return None
            if avg_rating >= negative_threshold:
                return None

        # Ensure all ratings have non-empty comments
        if not validate_ratings(professor.ratings):
            return None

        # Extract data
        professor_rows = extract_professor_data(professor)
        if professor_rows:
            return professor_rows

        return None

    except Exception as e:
        # Log the exception with professor ID
        logging.error(f"Error processing professor ID {prof_id}: {e}")
        return None

def initialize_csv(csv_filename, headers):
    """
    Initializes the CSV file with headers.
    """
    # If the CSV already exists, remove it to start fresh
    if os.path.exists(csv_filename):
        os.remove(csv_filename)
    
    # Write headers to CSV
    with open(csv_filename, mode='w', newline='', encoding='utf-8') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=headers)
        writer.writeheader()

def append_rows_to_csv(csv_filename, rows, headers):
    """
    Appends a list of dictionaries to the CSV file.
    """
    if not rows:
        return
    
    with open(csv_filename, mode='a', newline='', encoding='utf-8') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=headers)
        writer.writerows(rows)

def batched(iterable, n):
    """Yield successive n-sized batches from iterable."""
    for i in range(0, len(iterable), n):
        yield iterable[i:i + n]

## Data Fetching and Processing

Now, we'll set up the logging configuration, initialize the CSV file, and prepare to fetch professor data using concurrency for efficiency. We'll use `ThreadPoolExecutor` to handle multiple threads, allowing us to process multiple professor IDs simultaneously.

We'll also implement a progress bar using `tqdm` to monitor the progress of our data collection.

In [ ]:
# Setup logging for general data collection
setup_logging(LOG_FILENAME_GENERAL)

collected_professors_general = 0
target_reached_general = False

# Create a list of all IDs to process for general data
all_ids_general = list(range(START_ID_GENERAL, END_ID_GENERAL + 1))
total_ids_general = len(all_ids_general)

# Define headers based on expected data structure for general data
headers_general = [
    'professor_id', 'department', 'first_name', 'last_name', 'would_take_again_percent',
    'avg_rating', 'num_ratings',
    'school_legacyId', 'school_name', 'school_city', 'school_state', 'school_country',
    'school_id', 'school_avgRating', 'school_numRatings',
    'rating_comment', 'rating_flagStatus', 'rating_createdByUser', 'rating_date',
    'rating_class', 'rating_helpfulRating', 'rating_clarityRating', 'rating_isForOnlineClass',
    'rating_difficultyRating', 'rating_attendanceMandatory', 'rating_textbookUse',
    'rating_isForCredit'
]

# Initialize CSV with headers for general data
initialize_csv(CSV_FILENAME_GENERAL, headers_general)

# Initialize progress bar for general data collection
pbar_general = tqdm(total=total_ids_general, desc='Processing General Professors')

# Configuration dictionary for general data collection
config_general = {
    'MIN_RATINGS': MIN_RATINGS_GENERAL,
    'IS_NEGATIVE': False
}

# Use ThreadPoolExecutor for batch processing
with concurrent.futures.ThreadPoolExecutor(max_workers=MAX_WORKERS_GENERAL) as executor:
    # Process IDs in batches
    for batch in batched(all_ids_general, BATCH_SIZE_GENERAL):
        if collected_professors_general >= TARGET_PROFESSORS_GENERAL:
            break

        # Submit all fetch tasks for the current batch
        future_to_id = {executor.submit(fetch_and_filter_professor, prof_id, config_general): prof_id for prof_id in batch}
        
        # Process completed futures as they finish
        for future in concurrent.futures.as_completed(future_to_id):
            prof_id = future_to_id[future]
            try:
                result = future.result()
                if result:
                    # Append rows to CSV incrementally
                    append_rows_to_csv(CSV_FILENAME_GENERAL, result, headers_general)
                    collected_professors_general += 1
                    if collected_professors_general >= TARGET_PROFESSORS_GENERAL:
                        target_reached_general = True
                        break
            except Exception as e:
                # Log the exception with professor ID
                logging.error(f"Exception for professor ID {prof_id}: {e}")
                pass
            finally:
                pbar_general.update(1)
        
        if target_reached_general:
            break

pbar_general.close()

if collected_professors_general == 0:
    print("No professors met the general criteria.")
else:
    print(f"Successfully saved data for {collected_professors_general} general professors to '{CSV_FILENAME_GENERAL}'.")

## Addressing Rating Imbalance: Collecting Negative Ratings

After performing some Exploratory Data Analysis (EDA) on the collected data, it was observed that there's an imbalance between positive and negative ratings. To address this imbalance, we'll collect an additional 25,000 rows of professors with predominantly negative ratings.

This section will guide you through configuring the parameters for negative ratings, defining any additional helper functions if necessary, and fetching the negative ratings data.

### Configuration for Negative Ratings

We've already defined the necessary constants for collecting negative ratings in the [Configuration](#Configuration) section. These include the range of professor IDs to process, the target number of negative professors, the minimum number of ratings required, the threshold for what constitutes a negative average rating, filenames for the CSV and log files, batch sizes, and the number of worker threads.

### Defining Helper Functions for Negative Ratings

Since we've already defined generalized helper functions that can be parameterized based on the configuration, we don't need to redefine them for negative ratings. We'll reuse the existing `fetch_and_filter_professor` function by passing appropriate configuration parameters.

### Data Fetching and Processing for Negative Ratings

Now, we'll set up the logging configuration, initialize the CSV file for negative ratings, and prepare to fetch professor data using concurrency. Similar to the general data collection, we'll use `ThreadPoolExecutor` and `tqdm` for efficiency and progress monitoring.

In [5]:
# Setup logging for negative data collection
setup_logging(LOG_FILENAME_NEGATIVE)

collected_professors_negative = 0
target_reached_negative = False

# Create a list of all IDs to process for negative data
all_ids_negative = list(range(START_ID_NEGATIVE, END_ID_NEGATIVE + 1))
total_ids_negative = len(all_ids_negative)

# Define headers based on expected data structure for negative data
headers_negative = [
    'professor_id', 'department', 'first_name', 'last_name', 'would_take_again_percent',
    'avg_rating', 'num_ratings',
    'school_legacyId', 'school_name', 'school_city', 'school_state', 'school_country',
    'school_id', 'school_avgRating', 'school_numRatings',
    'rating_comment', 'rating_flagStatus', 'rating_createdByUser', 'rating_date',
    'rating_class', 'rating_helpfulRating', 'rating_clarityRating', 'rating_isForOnlineClass',
    'rating_difficultyRating', 'rating_attendanceMandatory', 'rating_textbookUse',
    'rating_isForCredit'
]

# Initialize CSV with headers for negative data
initialize_csv(CSV_FILENAME_NEGATIVE, headers_negative)

# Initialize progress bar for negative data collection
pbar_negative = tqdm(total=total_ids_negative, desc='Processing Negative Professors')

# Configuration dictionary for negative data collection
config_negative = {
    'MIN_RATINGS': MIN_RATINGS_NEGATIVE,
    'NEGATIVE_RATING_THRESHOLD': NEGATIVE_RATING_THRESHOLD,
    'IS_NEGATIVE': True
}

# Use ThreadPoolExecutor for batch processing
with concurrent.futures.ThreadPoolExecutor(max_workers=MAX_WORKERS_NEGATIVE) as executor:
    # Process IDs in batches
    for batch in batched(all_ids_negative, BATCH_SIZE_NEGATIVE):
        if collected_professors_negative >= TARGET_PROFESSORS_NEGATIVE:
            break

        # Submit all fetch tasks for the current batch
        future_to_id = {executor.submit(fetch_and_filter_professor, prof_id, config_negative): prof_id for prof_id in batch}
        
        # Process completed futures as they finish
        for future in concurrent.futures.as_completed(future_to_id):
            prof_id = future_to_id[future]
            try:
                result = future.result()
                if result:
                    # Append rows to CSV incrementally
                    append_rows_to_csv(CSV_FILENAME_NEGATIVE, result, headers_negative)
                    collected_professors_negative += 1
                    if collected_professors_negative >= TARGET_PROFESSORS_NEGATIVE:
                        target_reached_negative = True
                        break
            except Exception as e:
                # Log the exception with professor ID
                logging.error(f"Exception for professor ID {prof_id}: {e}")
                pass
            finally:
                pbar_negative.update(1)
        
        if target_reached_negative:
            break

pbar_negative.close()

if collected_professors_negative == 0:
    print("No professors met the negative criteria.")
else:
    print(f"Successfully saved data for {collected_professors_negative} negative professors to '{CSV_FILENAME_NEGATIVE}'.")


Processing Negative Professors:   0%|                                                       | 0/500000 [00:00<?, ?it/s]

Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve t

Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404


Failed to retrieve the webpage. Status code: 404
Failed to retrieve the webpage. Status code: 404



Processing Negative Professors:   0%|                                           | 1/500000 [00:02<340:25:57,  2.45s/it]

...


Processing Negative Professors:  32%|████████████▏                         | 160545/500000 [1:39:32<2:29:02, 37.96it/s]


Processing Negative Professors:  32%|████████████▏                         | 160557/500000 [1:39:33<2:07:45, 44.28it/s]


Processing Negative Professors:  32%|████████████▏                         | 160568/500000 [1:39:33<1:51:40, 50.65it/s]


Processing Negative Professors:  32%|████████████▏                         | 160571/500000 [1:39:33<3:30:27, 26.88it/s]

Successfully saved data for 6000 negative professors to 'negative_professors_6k.csv'.


## Data Merging and Finalization

With both datasets collected—general and negative ratings—we'll proceed to merge them into a single comprehensive dataset. This will facilitate more robust analysis and ensure that our dataset is balanced in terms of positive and negative ratings.

In [ ]:
# Load the general CSV file
df_general = pd.read_csv(CSV_FILENAME_GENERAL) # 'professors_50000.csv'

# Load the negative CSV file
df_negative = pd.read_csv(CSV_FILENAME_NEGATIVE) # 'negative_professors_25000.csv'

# Concatenate both dataframes
df_merged_final = pd.concat([df_general, df_negative], ignore_index=True)

# Save the final merged dataframe to a new CSV file
final_csv_filename = 'professors_75346.csv'
df_merged_final.to_csv(final_csv_filename, index=False)

print(f"Successfully merged data into '{final_csv_filename}'.")

Successfully merged data into 'professors_75346.csv'.


## Conclusion

Congratulations! You've successfully set up and executed a data collection pipeline to fetch and process professor data from the RateMyProfessor API, addressing the initial imbalance in ratings by collecting additional negative ratings data.

### Next Steps

- **Data Analysis:** Use the collected CSV data (`professors_75000_balanced.csv`) to perform various analyses, such as identifying trends in professor ratings, departmental comparisons, and more.
- **Visualization:** Create visualizations to represent the data graphically, making insights easier to understand.
- **Error Handling Improvements:** Enhance the error handling mechanisms to manage different types of exceptions more gracefully.
- **Optimization:** Further optimize the data fetching process by experimenting with different batch sizes and worker counts.

Feel free to explore and expand upon this foundation to suit your specific needs and interests!

## Appendix: Fetching a Single Professor (Optional)

If you'd like to test the API and see how data for a single professor looks before running the entire data collection process, you can use the following code snippet. Replace `prof_id` with a valid professor ID to fetch and inspect their data.

In [7]:
prof_id = 2000002  # Replace with a valid professor ID
professor = RateMyProfessor_Database_APIs.fetch_a_professor(prof_id)

# Display the fetched professor data
import pprint
pprint.pprint(professor.__dict__)  # Assuming the professor object has a __dict__ attribute

{'avg_difficulty': 2.8,
 'avg_rating': 4,
 'course_codes': [{'courseCount': 8, 'courseName': 'ENG131'},
                  {'courseCount': 2, 'courseName': 'ENG132'}],
 'department': 'English',
 'department_id': '18',
 'first_name': 'Rusty',
 'id': 'VGVhY2hlci0yMDAwMDAy',
 'is_prof_current_user': False,
 'is_saved': False,
 'last_name': 'Spell',
 'legacy_id': 2000002,
 'lock_status': 'none',
 'num_ratings': 10,
 'ratings': [{'attendanceMandatory': '',
              'clarityRating': 5,
              'class': 'ENG131',
              'comment': 'He was a really good professor. Always let us revise '
                         'and gave us opportunity to let him look over essays '
                         'before turning in. We were able to get a couple '
                         'extra credit points. Referred a lot back to The '
                         'Little Seagull handbook. Wasnt bad at all.',
              'createdByUser': False,
              'date': '2022-01-26 06:39:53 +0000 UTC',
 

This optional section allows you to verify that the API is working correctly and understand the structure of the data you're working with.